In [173]:
import argparse, time
import numpy as np
import pandas as pd
import networkx as nx
import torch
import torch.nn as nn
import torch.nn.functional as F
import dgl.function as fn
from dgl import DGLGraph
from dgl.data import register_data_args, load_data
from tqdm import tqdm
import scipy.sparse as sp
from datetime import datetime
import math
from torch.utils.data import Dataset
%matplotlib inline

from GCN import Net
from torch.utils.data import DataLoader
from dataUtils import loadEnergyData, processData, energyDataset
from modelUtils import saveCheckpoint, loadCheckpoint, plotPredVsTrue

In [3]:
processed_dir = "data/"
validation_range = ["2014-10-01 00:00:00", "2014-12-31 23:00:00"]
validation_range = [datetime.strptime(date, '%Y-%m-%d %H:%M:%S') for date in validation_range]

In [146]:
class DGL_EnergyDataset(Dataset):
    def __int__(self,args=None,processing_function=None):
        self.args = args
        self.processing_function=processing_function
    def __len__(self):
        return len(self.inputs)
    
    def __getitem__(self,index):
        return self.inputs[index],self.targets[index]
    
    def process(self,df):
        #df = self.processing_function(df)
        #print("Processed Data")
        grouped = df.groupby('time')
        inputs = []
        targets = []
        for time, group in tqdm(grouped):
            group.node = group.node.astype('int64')
            group = group.sort_values('node')


            node_targets = group.load.values
            #print(group.loc[group.time==time,['solar_ecmwf','wind_ecmwf','holiday','hour','dow','month','year',
                                          #'season','country','voltage']].values)
            node_features = group.loc[group.time==time,['solar_ecmwf','wind_ecmwf','holiday','hour','dow','month','year',
                                          'season','country','voltage']].values

            node_features = torch.from_numpy(np.array(node_features))
            node_targets = torch.from_numpy(np.array(node_targets))
           
            inputs.append(node_features)
            targets.append(node_targets)
        #print(torch.stack(inputs).transpose(0,1).shape) 
        #print(torch.stack(inputs).shape)
        self.inputs,self.targets = torch.stack(inputs), \
        torch.stack(targets)
        self.inputs = self.inputs.type(torch.FloatTensor)
        self.targets = self.targets.type(torch.FloatTensor)
        

In [147]:
def getDatasets(energy_demand, validation_range):
    energy_demand['time'] = pd.to_datetime(energy_demand['time'], format='%Y-%m-%d %H:%M:%S')
    
    # extract validation and training sets
    train_df = energy_demand[energy_demand['time'] < validation_range[0]].reset_index(drop = True)
    val_df = energy_demand[(energy_demand['time'] >= validation_range[0]) & 
                           (energy_demand['time'] <= validation_range[1])].reset_index(drop = True)
    
    train_dataset = DGL_EnergyDataset()
    valid_dataset = DGL_EnergyDataset()
    train_dataset.process(train_df)
    valid_dataset.process(val_df)
    #print(valid_dataset)
    #train_dataset = train_dataset.type(torch.FloatTensor)
    #valid_dataset = valid_dataset.type(torch.FloatTensor)


    return train_dataset,valid_dataset

In [6]:
#load data
energy_demand, adj_mat = loadEnergyData(processed_dir, incl_nodes = 300, partial = True)
#bacis preprocessing and normalization
energy_demand = processData(energy_demand)
#train_dataset,val_dataset = getDatasets(energy_demand)
#train_loader = DataLoader(train_dataset, batch_size=args.batch_size, shuffle=True)
#val_loader = DataLoader(val_dataset, batch_size=args.batch_size, shuffle=False)

In [58]:
energy_demand

node                time  solar_ecmwf  wind_ecmwf  holiday      hour  \
0          1 2012-01-01 00:00:00          0.0      0.0284        1  0.000000   
1          1 2012-01-01 01:00:00          0.0      0.0336        1  0.043478   
2          1 2012-01-01 02:00:00          0.0      0.0392        1  0.086957   
3          1 2012-01-01 03:00:00          0.0      0.0424        1  0.130435   
4          1 2012-01-01 04:00:00          0.0      0.0475        1  0.173913   
...      ...                 ...          ...         ...      ...       ...   
499771    19 2014-12-31 19:00:00          0.0      0.0305        0  0.826087   
499772    19 2014-12-31 20:00:00          0.0      0.0479        0  0.869565   
499773    19 2014-12-31 21:00:00          0.0      0.0567        0  0.913043   
499774    19 2014-12-31 22:00:00          0.0      0.0534        0  0.956522   
499775    19 2014-12-31 23:00:00          0.0      0.0403        0  1.000000   

             dow  month  year  season  country  voltage      load  
0       1.000000    0.0   0.0     1.0      0.0      0.0  0.036393  
1       1.000000    0.0   0.0     1.0      0.0      0.0  0.033963  
2       1.000000    0.0   0.0     1.0      0.0      0.0  0.031690  
3       1.000000    0.0   0.0     1.0      0.0      0.0  0.029789  
4       1.000000    0.0   0.0     1.0      0.0      0.0  0.028787  
...          ...    ...   ...     ...      ...      ...       ...  
499771  0.333333    1.0   1.0     1.0      0.0      0.0  0.079104  
499772  0.333333    1.0   1.0     1.0      0.0      0.0  0.076119  
499773  0.333333    1.0   1.0     1.0      0.0      0.0  0.068698  
499774  0.333333    1.0   1.0     1.0      0.0      0.0  0.064993  
499775  0.333333    1.0   1.0     1.0      0.0      0.0  0.062923  

[499776 rows x 13 columns]

In [148]:
train_dataset,val_dataset = getDatasets(energy_demand,validation_range)

100%|██████████| 2208/2208 [00:07<00:00, 313.31it/s]


In [151]:
train_loader = DataLoader(train_dataset, batch_size=1, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=1, shuffle=False)


In [174]:
num_of_nodes = train_dataset.inputs.shape[1]
print(num_of_nodes)

19


In [108]:
edge_df = pd.read_csv(processed_dir+'network_edges.csv')
#just try partial data
edge_df = edge_df[edge_df.fromNode<20]
edge_df = edge_df[edge_df.toNode <20]
edge_df

fromNode  toNode         X           Y  numLines  limit     length
883          1       2  0.011732   85.233361         2    0.0  59.085085
1014         2       6  0.007836  127.614604         2    0.0  40.048424
1015        11       9  0.057340   17.439833         1    0.0  28.660726
1016        11      13  0.039110   25.568908         1    0.0  19.493166
1017        10      12  0.041510   24.090581         1    0.0  26.853622
1018        10       6  0.067380   14.841199         1    0.0  57.199251
1019        13       9  0.065380   15.295197         1    0.0  45.764499
1020        13      15  0.051416   19.449099         2    0.0  66.792045
1021        12      15  0.045950   21.762786         1    0.0  31.537087
1022        15      14  0.023900   41.841004         1    0.0  31.640303
1023        15      17  0.077510   12.901561         1    0.0  62.834849
1024        15      16  0.053260   18.775817         1    0.0  31.871357
1026        17      16  0.052770   18.950161         1    0.0  31.055319
1027        19      18  0.028870   34.638033         1    0.0  49.468381
1083         3       5  0.087010   11.492932         1    0.0  57.400077
1084         3       4  0.054090   18.487706         1    0.0  31.618266
1199         4       8  0.051364   19.468787         2    0.0  68.357393
1306         5       7  0.030860   32.404407         1    0.0  40.535414
1407         6       7  0.011493   87.010808         4    0.0  42.782274
1524         7       8  0.025536   39.160071         2    0.0  62.654566
1734         9       8  0.035065   28.518770         2    0.0  59.311794

In [ ]:
g = DGLGraph()
g.add_nodes(num_of_nodes)
g.add_edges(edge_df.fromNode-1,edge_df.toNode-1)

In [164]:
gcn_msg = fn.copy_src(src='h', out='m')
gcn_reduce = fn.sum(msg='m', out='h')

In [171]:
#define GCN model
class NodeApplyModule(nn.Module):
    def __init__(self, in_feats, out_feats, activation):
        super(NodeApplyModule, self).__init__()
        self.linear = nn.Linear(in_feats, out_feats)
        self.activation = activation

    def forward(self, node):
        h = self.linear(node.data['h'])
        if self.activation is not None:
            h = self.activation(h)
        return {'h' : h}
    
class GCN(nn.Module):
    def __init__(self, in_feats, out_feats, activation):
        super(GCN, self).__init__()
        self.apply_mod = NodeApplyModule(in_feats, out_feats, activation)

    def forward(self, g, feature):
        g.ndata['h'] = feature
        g.update_all(gcn_msg, gcn_reduce)
        g.apply_nodes(func=self.apply_mod)
        return g.ndata.pop('h')
    
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.gcn1 = GCN(10, 16, F.relu)
        self.gcn2 = GCN(16, 1, None)

    def forward(self, g, features):
        x = self.gcn1(g, features)
        x = self.gcn2(g, x)
        return x

In [172]:
net = Net()
print(net)

Net(
  (gcn1): GCN(
    (apply_mod): NodeApplyModule(
      (linear): Linear(in_features=10, out_features=16, bias=True)
    )
  )
  (gcn2): GCN(
    (apply_mod): NodeApplyModule(
      (linear): Linear(in_features=16, out_features=1, bias=True)
    )
  )
)


In [170]:
#main _ train
criterion = torch.nn.MSELoss()
avg_trn_loss = AverageMeter()
avg_val_loss = AverageMeter()
epoch_trn_loss = []
epoch_val_loss = []
    
# use optimizer
optimizer = torch.optim.Adam(model.parameters(),
                                 lr=.01,
                                 weight_decay=5e-4)
train_loss = []
val_loss = []
val_best = 1
# initialize graph
for epoch in range(2):
    model.train()
    for batch_idx, (inputs, targets) in enumerate(train_loader):
        inputs = inputs.to('cpu')
        targets = targets.to('cpu')
        
        optimizer.zero_grad()
        
        #print(inputs.shape)
        predicted = net(g,inputs[0])
        loss = criterion(predicted, targets)
        loss.backward()
        optimizer.step()
        
        # update tracking
        np_loss = loss.detach().cpu().numpy()
        avg_trn_loss.update(np_loss, 64)
        epoch_trn_loss.append(np_loss)
        print(f"Batch index {batch_idx} Out of {len(train_loader)}")
        print(f"Average Training Loss: {avg_trn_loss.avg}")

Batch index 0 Out of 24096
Average Training Loss: 0.05381813645362854
Batch index 1 Out of 24096
Average Training Loss: 0.04633974842727184
Batch index 2 Out of 24096
Average Training Loss: 0.038140413661797844
Batch index 3 Out of 24096
Average Training Loss: 0.034443559125065804
Batch index 4 Out of 24096
Average Training Loss: 0.036440560966730116
Batch index 5 Out of 24096
Average Training Loss: 0.032546503469347954
Batch index 6 Out of 24096
Average Training Loss: 0.03429439291357994
Batch index 7 Out of 24096
Average Training Loss: 0.03524878993630409
Batch index 8 Out of 24096
Average Training Loss: 0.03843315111266242
Batch index 9 Out of 24096
Average Training Loss: 0.03941379487514496
Batch index 10 Out of 24096
Average Training Loss: 0.04109157723459331
Batch index 11 Out of 24096
Average Training Loss: 0.039809126406908035
Batch index 12 Out of 24096
Average Training Loss: 0.03801226544265564
Batch index 13 Out of 24096
Average Training Loss: 0.036808637103864124
Batch inde

Batch index 139 Out of 24096
Average Training Loss: 0.0577920523072992
Batch index 140 Out of 24096
Average Training Loss: 0.05769326825830953
Batch index 141 Out of 24096
Average Training Loss: 0.057531080431711505
Batch index 142 Out of 24096
Average Training Loss: 0.057322508140981616
Batch index 143 Out of 24096
Average Training Loss: 0.05727668224264764
Batch index 144 Out of 24096
Average Training Loss: 0.057183419129457964
Batch index 145 Out of 24096
Average Training Loss: 0.05704447653859037
Batch index 146 Out of 24096
Average Training Loss: 0.05712486181382825
Batch index 147 Out of 24096
Average Training Loss: 0.056855140593708366
Batch index 148 Out of 24096
Average Training Loss: 0.056631693103969497
Batch index 149 Out of 24096
Average Training Loss: 0.05673719023664792
Batch index 150 Out of 24096
Average Training Loss: 0.05664097068720306
Batch index 151 Out of 24096
Average Training Loss: 0.05644530043202011
Batch index 152 Out of 24096
Average Training Loss: 0.056217

Batch index 290 Out of 24096
Average Training Loss: 0.055296013675809316
Batch index 291 Out of 24096
Average Training Loss: 0.055203740536043905
Batch index 292 Out of 24096
Average Training Loss: 0.055068890014250124
Batch index 293 Out of 24096
Average Training Loss: 0.05500363039651087
Batch index 294 Out of 24096
Average Training Loss: 0.05507233181368496
Batch index 295 Out of 24096
Average Training Loss: 0.055032199267549695
Batch index 296 Out of 24096
Average Training Loss: 0.055010507635847486
Batch index 297 Out of 24096
Average Training Loss: 0.05527120271710141
Batch index 298 Out of 24096
Average Training Loss: 0.05522047195670796
Batch index 299 Out of 24096
Average Training Loss: 0.055246228085209924
Batch index 300 Out of 24096
Average Training Loss: 0.055364397431776374
Batch index 301 Out of 24096
Average Training Loss: 0.055282547076954354
Batch index 302 Out of 24096
Average Training Loss: 0.055223427337929364
Batch index 303 Out of 24096
Average Training Loss: 0.0

Batch index 470 Out of 24096
Average Training Loss: 0.05499036453126469
Batch index 471 Out of 24096
Average Training Loss: 0.05493582112683078
Batch index 472 Out of 24096
Average Training Loss: 0.05485940629706952
Batch index 473 Out of 24096
Average Training Loss: 0.054841549662315144
Batch index 474 Out of 24096
Average Training Loss: 0.055121635053502885
Batch index 475 Out of 24096
Average Training Loss: 0.05507489811519489
Batch index 476 Out of 24096
Average Training Loss: 0.0550516082922805
Batch index 477 Out of 24096
Average Training Loss: 0.05524158949679286
Batch index 478 Out of 24096
Average Training Loss: 0.05528282493523989
Batch index 479 Out of 24096
Average Training Loss: 0.05522370811474199
Batch index 480 Out of 24096
Average Training Loss: 0.055459439053573874
Batch index 481 Out of 24096
Average Training Loss: 0.055565306503341155
Batch index 482 Out of 24096
Average Training Loss: 0.05555913052434877
Batch index 483 Out of 24096
Average Training Loss: 0.0555116

Batch index 599 Out of 24096
Average Training Loss: 0.05652490928458671
Batch index 600 Out of 24096
Average Training Loss: 0.05648693515796729
Batch index 601 Out of 24096
Average Training Loss: 0.05660371209163701
Batch index 602 Out of 24096
Average Training Loss: 0.05659923123915496
Batch index 603 Out of 24096
Average Training Loss: 0.05655634893560844
Batch index 604 Out of 24096
Average Training Loss: 0.05658375490918632
Batch index 605 Out of 24096
Average Training Loss: 0.05652972371025448
Batch index 606 Out of 24096
Average Training Loss: 0.05647154426420049
Batch index 607 Out of 24096
Average Training Loss: 0.05648500903962964
Batch index 608 Out of 24096
Average Training Loss: 0.05642707987530968
Batch index 609 Out of 24096
Average Training Loss: 0.0564136006090729
Batch index 610 Out of 24096
Average Training Loss: 0.05637351875597346
Batch index 611 Out of 24096
Average Training Loss: 0.0563589036373385
Batch index 612 Out of 24096
Average Training Loss: 0.056474337609

...

Batch index 23414 Out of 24096
Average Training Loss: 0.05827790066509754
Batch index 23415 Out of 24096
Average Training Loss: 0.05827746160728187
Batch index 23416 Out of 24096
Average Training Loss: 0.05827674669276768
Batch index 23417 Out of 24096
Average Training Loss: 0.058276615216765915
Batch index 23418 Out of 24096
Average Training Loss: 0.05827640852773599
Batch index 23419 Out of 24096
Average Training Loss: 0.05827629778750795
Batch index 23420 Out of 24096
Average Training Loss: 0.058275887946809456
Batch index 23421 Out of 24096
Average Training Loss: 0.058275045219744845
Batch index 23422 Out of 24096
Average Training Loss: 0.0582782199691986
Batch index 23423 Out of 24096
Average Training Loss: 0.058277738652006264
Batch index 23424 Out of 24096
Average Training Loss: 0.05828060016292142
Batch index 23425 Out of 24096
Average Training Loss: 0.058280186572958255
Batch index 23426 Out of 24096
Average Training Loss: 0.05827993667957427
Batch index 23427 Out of 24096
Ave

Batch index 23570 Out of 24096
Average Training Loss: 0.058270901305413084
Batch index 23571 Out of 24096
Average Training Loss: 0.05827021784500164
Batch index 23572 Out of 24096
Average Training Loss: 0.05826962738973264
Batch index 23573 Out of 24096
Average Training Loss: 0.058271719366941116
Batch index 23574 Out of 24096
Average Training Loss: 0.05827110577307491
Batch index 23575 Out of 24096
Average Training Loss: 0.058270816236948034
Batch index 23576 Out of 24096
Average Training Loss: 0.05827014437849233
Batch index 23577 Out of 24096
Average Training Loss: 0.05826944575854486
Batch index 23578 Out of 24096
Average Training Loss: 0.05826914349491755
Batch index 23579 Out of 24096
Average Training Loss: 0.05826886379144672
Batch index 23580 Out of 24096
Average Training Loss: 0.05826873690873093
Batch index 23581 Out of 24096
Average Training Loss: 0.058268297037647375
Batch index 23582 Out of 24096
Average Training Loss: 0.0582679654671303
Batch index 23583 Out of 24096
Aver

Batch index 23685 Out of 24096
Average Training Loss: 0.05829716402940478
Batch index 23686 Out of 24096
Average Training Loss: 0.058296423480837745
Batch index 23687 Out of 24096
Average Training Loss: 0.05829836775719647
Batch index 23688 Out of 24096
Average Training Loss: 0.05829824800929059
Batch index 23689 Out of 24096
Average Training Loss: 0.058297753883842625
Batch index 23690 Out of 24096
Average Training Loss: 0.05829999866875557
Batch index 23691 Out of 24096
Average Training Loss: 0.05830187130527811
Batch index 23692 Out of 24096
Average Training Loss: 0.05830124225007911
Batch index 23693 Out of 24096
Average Training Loss: 0.05830053434568666
Batch index 23694 Out of 24096
Average Training Loss: 0.05830013679120235
Batch index 23695 Out of 24096
Average Training Loss: 0.0582998306650664
Batch index 23696 Out of 24096
Average Training Loss: 0.05829985342932922
Batch index 23697 Out of 24096
Average Training Loss: 0.05830013941385433
Batch index 23698 Out of 24096
Averag

Batch index 23800 Out of 24096
Average Training Loss: 0.058297186279249215
Batch index 23801 Out of 24096
Average Training Loss: 0.05829674271601698
Batch index 23802 Out of 24096
Average Training Loss: 0.05829631944142985
Batch index 23803 Out of 24096
Average Training Loss: 0.058295992261385994
Batch index 23804 Out of 24096
Average Training Loss: 0.05829534337962169
Batch index 23805 Out of 24096
Average Training Loss: 0.058294701331874955
Batch index 23806 Out of 24096
Average Training Loss: 0.05829426402560218
Batch index 23807 Out of 24096
Average Training Loss: 0.05829512633641612
Batch index 23808 Out of 24096
Average Training Loss: 0.05829432506626321
Batch index 23809 Out of 24096
Average Training Loss: 0.05829351216258211
Batch index 23810 Out of 24096
Average Training Loss: 0.058293733589202965
Batch index 23811 Out of 24096
Average Training Loss: 0.058295965769576304
Batch index 23812 Out of 24096
Average Training Loss: 0.05829559762925286
Batch index 23813 Out of 24096
Av

Batch index 23965 Out of 24096
Average Training Loss: 0.05830323099494749
Batch index 23966 Out of 24096
Average Training Loss: 0.058305675906590144
Batch index 23967 Out of 24096
Average Training Loss: 0.058305149527682676
Batch index 23968 Out of 24096
Average Training Loss: 0.0583047966776722
Batch index 23969 Out of 24096
Average Training Loss: 0.058304235346992604
Batch index 23970 Out of 24096
Average Training Loss: 0.05830387915725154
Batch index 23971 Out of 24096
Average Training Loss: 0.058303899993597495
Batch index 23972 Out of 24096
Average Training Loss: 0.05830424506123545
Batch index 23973 Out of 24096
Average Training Loss: 0.058303718968438514
Batch index 23974 Out of 24096
Average Training Loss: 0.05830458305837031
Batch index 23975 Out of 24096
Average Training Loss: 0.05830415875535786
Batch index 23976 Out of 24096
Average Training Loss: 0.058303710650628233
Batch index 23977 Out of 24096
Average Training Loss: 0.05830351648723672
Batch index 23978 Out of 24096
Av